In [36]:
def data_size(x, metric="b"):
    size_bytes = x.element_size() * x.nelement()
    size_kb = size_bytes / (1024)
    size_mb = size_bytes / (1024 ** 2)
    if metric == "b":
        return size_bytes
    elif metric == "kb":
        return size_kb
    else: 
        return size_mb 

In [157]:
import json
import numpy as np 
import base64
import io

def get_inference_request_data(simulation, client_id=0, sample_id=0):
    client = simulation.client_datasets[client_id]
    tensor = client.test_dataset[sample_id][0]  # Assume PyTorch tensor
    np_array = tensor.numpy().astype(np.float32)
    return np_array

def send_inference_request(client_id, sample_id, client_data, use_file=False):
    if use_file:
        # Save numpy array as .npy in-memory file and get size
        buffer = io.BytesIO()
        np.save(buffer, client_data)
        buffer.seek(0)
        file_bytes = buffer.read()
        
        file_size = len(file_bytes)
        headers = {
            "Content-Type": "application/octet-stream",
            "Content-Disposition": f"attachment; filename=client_{client_id}_sample_{sample_id}.npy"
        }
        headers_size = sum(len(k) + len(v) + 4 for k, v in headers.items())
        total_request_size = file_size + headers_size
        
        print(f"[CLIENT {client_id} Send inference request as .npy file] Estimated total request size: {total_request_size / 1024:.2f} KB")
        return total_request_size
    
    else:
        # existing base64 JSON method
        byte_data = client_data.tobytes()
        base64_data = base64.b64encode(byte_data).decode('utf-8')
        shape = [int(dim) for dim in client_data.shape]

        data = {
            "client_id": int(client_id),
            "sample_id": int(sample_id),
            "local_data": {
                "data": base64_data,
                "shape": shape,
                "dtype": str(client_data.dtype)
            }
        }
        json_data = json.dumps(data)
        data_bytes = json_data.encode("utf-8")
        headers = {"Content-Type": "application/json"}
        request_body_size = len(data_bytes)
        headers_size = sum(len(k) + len(v) + 4 for k, v in headers.items())
        total_request_size = request_body_size + headers_size
        
        print(f"[CLIENT {client_id} Send inference request as JSON base64] Estimated total request size: {total_request_size / 1024:.2f} KB")
        return total_request_size

def request_local_data(sample_id = 0):
    data = {
        "sample_id": sample_id,
    } 
    json_data = json.dumps(data)
    data_bytes = json_data.encode("utf-8")
    headers = {"Content-Type": "application/json"}
    # Estimate request size
    request_body_size = len(data_bytes)
    headers_size = sum(len(k) + len(v) + 4 for k, v in headers.items())  # Approx header size
    total_request_size = request_body_size + headers_size
    print(f"[SERVER Request Local data] Estimated total request size: {total_request_size / 1024:.2f} KB")
    return total_request_size


def response_local_data(client_id, sample_id, client_data, use_file=False):
    if use_file:
        # Save NumPy array as in-memory .npy file
        buffer = io.BytesIO()
        np.save(buffer, client_data)
        buffer.seek(0)
        file_bytes = buffer.read()

        headers = {
            "Content-Type": "application/octet-stream",
            "Content-Disposition": f"attachment; filename=client_{client_id}_sample_{sample_id}.npy"
        }
        headers_size = sum(len(k) + len(v) + 4 for k, v in headers.items())
        total_size = len(file_bytes) + headers_size

        print(f"[CLIENT {client_id} Send local response as .npy file] Estimated total request size: {total_size / 1024:.2f} KB")
        return total_size

    else:
        # Base64 encode as JSON
        byte_data = client_data.tobytes()
        base64_data = base64.b64encode(byte_data).decode('utf-8')
        shape = [int(dim) for dim in client_data.shape]

        data = {
            "client_id": int(client_id),
            "sample_id": int(sample_id),
            "local_data": {
                "data": base64_data,
                "shape": shape,
                "dtype": str(client_data.dtype)
            }
        }

        json_data = json.dumps(data)
        data_bytes = json_data.encode("utf-8")
        headers = {"Content-Type": "application/json"}

        request_body_size = len(data_bytes)
        headers_size = sum(len(k) + len(v) + 4 for k, v in headers.items())
        total_request_size = request_body_size + headers_size

        print(f"[CLIENT {client_id} Send local response as JSON base64] Estimated total request size: {total_request_size / 1024:.2f} KB")
        return total_request_size

def response_target():
    data = {
        "target_id": int(0),
    } 
    json_data = json.dumps(data)
    data_bytes = json_data.encode("utf-8")
    headers = {"Content-Type": "application/json"}
    # Estimate request size
    request_body_size = len(data_bytes)
    headers_size = sum(len(k) + len(v) + 4 for k, v in headers.items())  # Approx header size
    total_request_size = request_body_size + headers_size
    print(f"[SERVER Response Target] Estimated total request size: {total_request_size / 1024:.2f} KB")
    return total_request_size


def on_cloud_inference_data_volume(simulation, client_id=0, sample_id=0, use_file=True):
    inference_data_volume = 0
    tensor = get_inference_request_data(simulation, client_id, sample_id)
    inference_data_volume += send_inference_request(client_id, sample_id, tensor, use_file=use_file)
    
    all_clients = list(range(len(simulation.client_datasets)))
    selected_clients = [client_id]
    remaining_clients = list(set(all_clients) - set(selected_clients))
    for i in remaining_clients:
        inference_data_volume += request_local_data(sample_id)
        tensor = get_inference_request_data(simulation, i, sample_id)  # Note: use correct client_id here
        inference_data_volume += response_local_data(i, sample_id, tensor, use_file=use_file)  # Could add use_file here too
    
    inference_data_volume += response_target()
    return inference_data_volume

def average_inference_data_volume(simulation, client_id=0, num_samples=1000):
    total_volume = 0

    for sample_id in range(num_samples):
        total_volume += on_cloud_inference_data_volume(simulation, client_id, sample_id)

    mean_volume = total_volume / num_samples
    return mean_volume  

In [160]:
DATASET = 'MNIST'
SEEDS = [4,13,27]
seed = 4
data_config = DataConfiguration(DATASET)
transform_config = DataTransformConfiguration()
simulation_on_cloud = OnCloudVerticalSimulation(seed, VERSION, data_config, transform_config, OnCloudMNISTModel, exist=False)
simulation_on_cloud.server.load()

MNIST training data loaded.
MNIST test data loaded.


In [161]:
average_inference_data_volume(simulation_on_cloud)

[CLIENT 0 Send inference request as .npy file] Estimated total request size: 0.99 KB
[SERVER Request Local data] Estimated total request size: 0.05 KB
[CLIENT 1 Send local response as .npy file] Estimated total request size: 0.99 KB
[SERVER Request Local data] Estimated total request size: 0.05 KB
[CLIENT 2 Send local response as .npy file] Estimated total request size: 0.99 KB
[SERVER Request Local data] Estimated total request size: 0.05 KB
[CLIENT 3 Send local response as .npy file] Estimated total request size: 0.99 KB
[SERVER Response Target] Estimated total request size: 0.05 KB
[CLIENT 0 Send inference request as .npy file] Estimated total request size: 0.99 KB
[SERVER Request Local data] Estimated total request size: 0.05 KB
[CLIENT 1 Send local response as .npy file] Estimated total request size: 0.99 KB
[SERVER Request Local data] Estimated total request size: 0.05 KB
[CLIENT 2 Send local response as .npy file] Estimated total request size: 0.99 KB
[SERVER Request Local data]

4273.23

# Upper Bound Analysis

In [162]:
import json
import numpy as np 
import base64

def get_inference_request_data(simulation, client_id=0, sample_id=0):
    client = simulation.client_datasets[client_id]
    tensor = client.test_dataset[sample_id][0]  # Assume this is a PyTorch tensor
    return tensor

def send_inference_request(client_id, sample_id, client_data):
    total_request_size = data_size(client_data)

    data = {
        "client_id": int(client_id),
        "sample_id": int(sample_id),
    }

    json_data = json.dumps(data)
    data_bytes = json_data.encode("utf-8")
    headers = {"Content-Type": "application/json"}

    request_body_size = len(data_bytes)
    headers_size = sum(len(k) + len(v) + 4 for k, v in headers.items())  # crude approximation
    total_request_size += request_body_size + headers_size
    print(f"[CLIENT {client_id} Send inference request] Estimated total request size: {total_request_size:.2f} B")
    return total_request_size

def request_local_data(sample_id = 0):
    data = {
        "sample_id": sample_id,
    } 
    json_data = json.dumps(data)
    data_bytes = json_data.encode("utf-8")
    headers = {"Content-Type": "application/json"}
    # Estimate request size
    request_body_size = len(data_bytes)
    headers_size = sum(len(k) + len(v) + 4 for k, v in headers.items())  # Approx header size
    total_request_size = request_body_size + headers_size
    print(f"[SERVER Request Local data] Estimated total request size: {total_request_size:.2f} B")
    return total_request_size


def response_local_data(client_id, sample_id, client_data):
    total_request_size = data_size(client_data)

    data = {
        "client_id": int(client_id),
        "sample_id": int(sample_id),
    }

    json_data = json.dumps(data)
    data_bytes = json_data.encode("utf-8")
    headers = {"Content-Type": "application/json"}

    request_body_size = len(data_bytes)
    headers_size = sum(len(k) + len(v) + 4 for k, v in headers.items())  # crude approximation
    total_request_size += request_body_size + headers_size

    print(f"[CLIENT {client_id} Send local response] Estimated total request size: {total_request_size:.2f} B")

    return total_request_size

def response_target():
    data = {
        "target_id": int(0),
    } 
    json_data = json.dumps(data)
    data_bytes = json_data.encode("utf-8")
    headers = {"Content-Type": "application/json"}
    # Estimate request size
    request_body_size = len(data_bytes)
    headers_size = sum(len(k) + len(v) + 4 for k, v in headers.items())  # Approx header size
    total_request_size = request_body_size + headers_size
    print(f"[SERVER Response Target] Estimated total request size: {total_request_size:.2f} B")
    return total_request_size


def on_cloud_inference_data_volume(simulation, client_id = 0, sample_id = 0):
    inference_data_volume = 0
    tensor_list = get_inference_request_data(simulation, client_id, sample_id)
    inference_data_volume += send_inference_request(client_id, sample_id, tensor_list)
    
    all_clients = list(range(len(simulation.client_datasets)))
    selected_clients = [client_id]
    remaining_clients = list(set(all_clients) - set(selected_clients))
    for i in remaining_clients:
        inference_data_volume += request_local_data(sample_id)
        tensor_list = get_inference_request_data(simulation, client_id, sample_id)
        inference_data_volume += response_local_data(i, sample_id, tensor_list)
    
    inference_data_volume += response_target()
    return inference_data_volume

def average_inference_data_volume(simulation, client_id=0, num_samples=1000):
    total_volume = 0

    for sample_id in range(num_samples):
        total_volume += on_cloud_inference_data_volume(simulation, client_id, sample_id)

    mean_volume = total_volume / num_samples
    return mean_volume  

In [163]:
average_inference_data_volume(simulation_on_cloud)

[CLIENT 0 Send inference request] Estimated total request size: 848.00 B
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 1 Send local response] Estimated total request size: 848.00 B
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 2 Send local response] Estimated total request size: 848.00 B
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 3 Send local response] Estimated total request size: 848.00 B
[SERVER Response Target] Estimated total request size: 48.00 B
[CLIENT 0 Send inference request] Estimated total request size: 848.00 B
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 1 Send local response] Estimated total request size: 848.00 B
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 2 Send local response] Estimated total request size: 848.00 B
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 3 Send local response] Estimated tota

3597.23

In [178]:
DATASET = 'FMNIST'
SEEDS = [4,13,27]
seed = 4
data_config = DataConfiguration(DATASET)
transform_config = DataTransformConfiguration()
simulation_on_cloud = OnCloudVerticalSimulation(seed, VERSION, data_config, transform_config, OnCloudMNISTModel, exist=False)
simulation_on_cloud.server.load()
average_inference_data_volume(simulation_on_cloud)

FashionMnist training data loaded.
FashionMnist training data loaded.
[CLIENT 0 Send inference request] Estimated total request size: 848.00 B
[City] Simulated upload time: 0.0001 s
[City] Simulated download time: 0.0001 s
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 1 Send local response] Estimated total request size: 848.00 B
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 1 Send local response] Estimated total request size: 848.00 B
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 2 Send local response] Estimated total request size: 848.00 B
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 2 Send local response] Estimated total request size: 848.00 B
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 3 Send local response] Estimated total request size: 848.00 B
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 3 Send local response] 

(3597.23, 0.5326429629629552)

In [167]:
DATASET = 'CIFAR10'
SEEDS = [4,13,27]
seed = 4
data_config = DataConfiguration(DATASET)
transform_config = DataTransformConfiguration()
simulation_on_cloud = OnCloudVerticalSimulation(seed, VERSION, data_config, transform_config, OnCloudMNISTModel, exist=False)
average_inference_data_volume(simulation_on_cloud)

CIFAR10 training data loaded.
CIFAR10 test data loaded.
[CLIENT 0 Send inference request] Estimated total request size: 2416.00 B
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 1 Send local response] Estimated total request size: 2416.00 B
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 2 Send local response] Estimated total request size: 2416.00 B
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 3 Send local response] Estimated total request size: 2416.00 B
[SERVER Response Target] Estimated total request size: 48.00 B
[CLIENT 0 Send inference request] Estimated total request size: 2416.00 B
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 1 Send local response] Estimated total request size: 2416.00 B
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 2 Send local response] Estimated total request size: 2416.00 B
[SERVER Request Local data] Estimated total requ

9869.23

# Inference Simulation

In [ ]:
def get_wlan_speed(environment='city'):
    """
    Returns average WLAN speed in Mbps depending on the environment.
    """
    speeds = {
        'rural': 10,     # Mbps, slower in rural areas
        'suburban': 30,  # Mbps, moderate in suburbs
        'city': 54       # Mbps, faster in city areas (e.g., typical 802.11g)
    }
    return speeds.get(environment.lower(), 54)  # default to city speed if unknown

def simulate_upload_download(total_request_size_bytes, environment='city'):
    """
    Simulate upload and download time based on request size and WLAN speed depending on environment.

    Args:
        total_request_size_bytes (int or float): Total size of request in bytes.
        environment (str): One of 'rural', 'suburban', 'city'.

    Returns:
        tuple: (upload_time_sec, download_time_sec)
    """
    wlan_speed_mbps = get_wlan_speed(environment)
    wlan_speed_bytes_per_sec = wlan_speed_mbps * 125000

    upload_time_sec = total_request_size_bytes / wlan_speed_bytes_per_sec
    download_time_sec = total_request_size_bytes / wlan_speed_bytes_per_sec

    print(f"[{environment.capitalize()}] Simulated upload time: {upload_time_sec:.4f} s")
    print(f"[{environment.capitalize()}] Simulated download time: {download_time_sec:.4f} s")

    return upload_time_sec, download_time_sec


import json
import numpy as np 
import base64

def get_inference_request_data(simulation, client_id=0, sample_id=0):
    client = simulation.client_datasets[client_id]
    tensor = client.test_dataset[sample_id][0]  # Assume this is a PyTorch tensor
    return tensor

def send_inference_request(client_id, sample_id, client_data):
    total_request_size = data_size(client_data)

    data = {
        "client_id": int(client_id),
        "sample_id": int(sample_id),
    }

    json_data = json.dumps(data)
    data_bytes = json_data.encode("utf-8")
    headers = {"Content-Type": "application/json"}

    request_body_size = len(data_bytes)
    headers_size = sum(len(k) + len(v) + 4 for k, v in headers.items())  # crude approximation
    total_request_size += request_body_size + headers_size
    print(f"[CLIENT {client_id} Send inference request] Estimated total request size: {total_request_size:.2f} B")
    return total_request_size

def on_cloud_inference_data_volume(simulation, client_id = 0, sample_id = 0):
    inference_data_volume = 0
    inference_time = 0

    # Inference Request
    tensor_list = get_inference_request_data(simulation, client_id, sample_id)
    total_request_size = send_inference_request(client_id, sample_id, tensor_list)
    inference_data_volume += total_request_size
    upload_time_sec, download_time_sec = simulate_upload_download(total_request_size, environment='city')
    inference_time += upload_time_sec + download_time_sec


    all_clients = list(range(len(simulation.client_datasets)))
    selected_clients = [client_id]
    remaining_clients = list(set(all_clients) - set(selected_clients))

    local_data_size = 0

    for i in remaining_clients:
        # Local Data Retrievals
        inference_data_volume += request_local_data(sample_id)
        tensor_list = get_inference_request_data(simulation, client_id, sample_id)
        inference_data_volume += response_local_data(i, sample_id, tensor_list)
        data_transfered = request_local_data(sample_id) + response_local_data(i, sample_id, tensor_list)
        local_data_size = max(local_data_size, data_transfered)
    
    upload_time_sec, download_time_sec = simulate_upload_download(local_data_size, environment='city')
    inference_time += upload_time_sec + download_time_sec

    # Target Response
    response_target_data = response_target()
    inference_data_volume += response_target_data

    upload_time_sec, download_time_sec = simulate_upload_download(response_target_data, environment='city')
    inference_time += upload_time_sec + download_time_sec

    return inference_data_volume, inference_time

def average_inference_data_volume(simulation, client_id=0, num_samples=1000):
    total_volume = 0
    total_time = 0

    for sample_id in range(num_samples):
        total_volume += on_cloud_inference_data_volume(simulation, client_id, sample_id)[0]
        total_time += on_cloud_inference_data_volume(simulation, client_id, sample_id)[1]

    mean_volume = total_volume / num_samples
    mean_time = total_time / num_samples
    return mean_volume, mean_time

average_inference_data_volume(simulation_on_cloud)

[CLIENT 0 Send inference request] Estimated total request size: 2416.00 B
[City] Simulated upload time: 0.0004 s
[City] Simulated download time: 0.0004 s
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 1 Send local response] Estimated total request size: 2416.00 B
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 1 Send local response] Estimated total request size: 2416.00 B
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 2 Send local response] Estimated total request size: 2416.00 B
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 2 Send local response] Estimated total request size: 2416.00 B
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 3 Send local response] Estimated total request size: 2416.00 B
[SERVER Request Local data] Estimated total request size: 48.00 B
[CLIENT 3 Send local response] Estimated total request size: 2416.00 B
[City] Simulated upload 

(9869.23, 1.4618281481481463)